In [1]:
import requests
import json
import pandas as pd
import numpy as np
from pandas.io.json import json_normalize
import os
import webbrowser
import folium
from folium import plugins
print(folium.__version__)

0.14.0


In [2]:
m = folium.Map(location=[36, 127], tiles="OpenStreetMap", zoom_start=7)

In [3]:
m

In [4]:
# folium.CircleMarker([37.5072384, 127.0238756],
#   radius=100,
#   color='blue',
#   fill_color='skyblue').add_to(m)

In [5]:
state_geo = 'sig_WGS84.json'

In [6]:
state_geo

'sig_WGS84.json'

In [7]:
state_data = pd.read_csv('Total_People_2023_2.csv', encoding = 'euc-kr')
state_data

CODE  POPULATION
0        0    51377213
1       11     9409466
2    11110      140032
3    11140      121482
4    11170      216547
..     ...         ...
287  48880       60184
288  48890       41531
289     50      676489
290  50110      492379
291  50130      184110

[292 rows x 2 columns]

In [8]:
import json

with open('sig_WGS84.json', 'r', encoding='utf-8') as f:

    json_data = json.load(f)

print(json.dumps(json_data) )

{"type": "FeatureCollection", "features": [{"type": "Feature", "geometry": {"type": "Polygon", "coordinates": [[[127.012, 37.582], [127.008, 37.581], [127.007, 37.582], [127.007, 37.584], [127.007, 37.585], [127.007, 37.586], [127.004, 37.588], [127.003, 37.588], [127.003, 37.589], [127.002, 37.589], [127.002, 37.59], [127.001, 37.59], [127.001, 37.591], [127.002, 37.591], [127.001, 37.592], [127, 37.592], [126.999, 37.592], [126.998, 37.592], [126.997, 37.592], [126.996, 37.592], [126.995, 37.592], [126.994, 37.592], [126.989, 37.592], [126.988, 37.592], [126.987, 37.593], [126.986, 37.593], [126.986, 37.594], [126.985, 37.594], [126.984, 37.594], [126.983, 37.595], [126.982, 37.595], [126.981, 37.595], [126.981, 37.596], [126.979, 37.596], [126.979, 37.597], [126.978, 37.597], [126.978, 37.598], [126.977, 37.598], [126.977, 37.599], [126.978, 37.6], [126.978, 37.601], [126.979, 37.601], [126.98, 37.601], [126.981, 37.602], [126.983, 37.602], [126.986, 37.603], [126.986, 37.604], [126

In [9]:
import json
json_data=open(state_geo, encoding='utf-8').read()
jsonResult = json.loads(json_data)

In [10]:
jsonResult

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[127.012, 37.582],
      [127.008, 37.581],
      [127.007, 37.582],
      [127.007, 37.584],
      [127.007, 37.585],
      [127.007, 37.586],
      [127.004, 37.588],
      [127.003, 37.588],
      [127.003, 37.589],
      [127.002, 37.589],
      [127.002, 37.59],
      [127.001, 37.59],
      [127.001, 37.591],
      [127.002, 37.591],
      [127.001, 37.592],
      [127, 37.592],
      [126.999, 37.592],
      [126.998, 37.592],
      [126.997, 37.592],
      [126.996, 37.592],
      [126.995, 37.592],
      [126.994, 37.592],
      [126.989, 37.592],
      [126.988, 37.592],
      [126.987, 37.593],
      [126.986, 37.593],
      [126.986, 37.594],
      [126.985, 37.594],
      [126.984, 37.594],
      [126.983, 37.595],
      [126.982, 37.595],
      [126.981, 37.595],
      [126.981, 37.596],
      [126.979, 37.596],
      [126.979, 37.597],
      [126.978, 3

In [11]:
# 중앙위치 계산
def center_calc(points_df):
    x = points_df.x
    y = points_df.y

    X = (max(x)+min(x))/2.
    Y = (max(y)+min(y))/2.

    return X, Y

In [12]:
# 다중 Array 구조 이중으로 변환
def points_array(points):

    final_points = []

    for x in range(0, len(points)):

        if len(points[x]) == 2:
            final_points.append(points[x])
        else:
            target = points[x]
            for y in range(0, len(target)):
                final_points.append(target[y])

    return final_points

In [13]:
center_locations = pd.DataFrame()
codes = []
names = []
x_list = []
y_list = []
for x in range(0, len(jsonResult['features'])):
    code = jsonResult['features'][x]['properties']['SIG_CD']
    name = jsonResult['features'][x]['properties']['SIG_KOR_NM']
    # 중앙값 생성
    points = jsonResult['features'][x]['geometry']['coordinates'][0]
    points = points_array(points)
    points_df = pd.DataFrame(points)
    points_df.columns = ['x','y']
    X, Y = center_calc(points_df)

    # 결과
    codes.append(code)
    names.append(name)
    x_list.append(X)
    y_list.append(Y)

# 데이터 프레임 생성
center_locations['CODE'] = codes
center_locations['NAME'] = names
center_locations['X'] = x_list
center_locations['Y'] = y_list

In [14]:
state_data.CODE.dtype

dtype('int64')

In [15]:
center_locations.CODE.dtype

dtype('O')

In [16]:
center_locations.CODE.dtype == state_data.CODE.dtype

False

In [240]:
import numpy as np

In [17]:
state_data.CODE = state_data.CODE.astype(str) 
#state_data.CODE.dtype

In [18]:
target_df = pd.merge(state_data,center_locations,on='CODE')
target_df

CODE  POPULATION  NAME         X        Y
0    11110      140032   종로구  126.9860  37.5990
1    11140      121482    중구  126.9945  37.5580
2    11170      216547   용산구  126.9815  37.5315
3    11200      278750   성동구  127.0415  37.5505
4    11215      336446   광진구  127.0855  37.5485
..     ...         ...   ...       ...      ...
245  48870       37117   함양군  127.7315  35.5435
246  48880       60184   거창군  127.8870  35.7120
247  48890       41531   합천군  128.1670  35.6000
248  50110      492379   제주시  126.2270  33.4085
249  50130      184110  서귀포시  126.2675  33.1180

[250 rows x 5 columns]

In [19]:
target_df = target_df[~np.isnan(target_df['X'])] # 위치 정보 없는 값 제외

In [20]:
target_df

CODE  POPULATION  NAME         X        Y
0    11110      140032   종로구  126.9860  37.5990
1    11140      121482    중구  126.9945  37.5580
2    11170      216547   용산구  126.9815  37.5315
3    11200      278750   성동구  127.0415  37.5505
4    11215      336446   광진구  127.0855  37.5485
..     ...         ...   ...       ...      ...
245  48870       37117   함양군  127.7315  35.5435
246  48880       60184   거창군  127.8870  35.7120
247  48890       41531   합천군  128.1670  35.6000
248  50110      492379   제주시  126.2270  33.4085
249  50130      184110  서귀포시  126.2675  33.1180

[250 rows x 5 columns]

In [21]:
# Initialize the map:
m = folium.Map(location=[36, 127], tiles="OpenStreetMap", zoom_start=7)


# I can add marker one by one on the map
for i in range(0,len(target_df)):
    latitude = target_df.iloc[i]['Y']
    longitude = target_df.iloc[i]['X']
    location=(latitude, longitude)
    folium.CircleMarker(location, radius=target_df.iloc[i]['POPULATION']/25000,color='green',fill_color='green', popup=target_df.iloc[i]['NAME']).add_to(m)
##location : 동그라미를 표시할 중심좌표 / radius : 동그라미 크기 / popup : 장소에 대한 세부정보 


folium.LayerControl(collapsed=False).add_to(m)



In [22]:
# Save to html
m.save(os.path.join('kr_polulation.html'))
m
# webbrowser.open_new("kr_polulation.html")